In [233]:
import folium
import branca
import pandas as pd
import numpy as np

### Crear unas variables globales

In [361]:
path_geojson = 'C:/Users/Ricardo/Documents/PROYECTO_FINAL/data/Londres/neighbourhoods.geojson'
london_coordinates = [51.5074,-0.1278]

### Esta casilla se tiene que borrar, se usara el listing limpio

In [25]:
listings_london = pd.read_csv('data/Londres/listings.csv')
listings_london['price'] = listings_london['price'].str[1:] 
listings_london['price'] = listings_london['price'].map(lambda x : x.replace(',',''))
listings_london['price'] = pd.to_numeric(listings_london['price'])

C:\Users\Ricardo\Anaconda4\lib\site-packages\IPython\core\interactiveshell.py:2785: DtypeWarning: Columns (61,62,94) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


# MAPA DE LOS VECINDARIOS MAS CAROS

### Crear una lista de los vecindarios mas caros

In [472]:
vecindarios_mas_costosos = list(listings_london.groupby('neighbourhood')['price'].mean().sort_values().index)
for v in vecindarios_mas_costosos:
    if '&' in v:
        i = vecindarios_mas_costosos.index(v)
        vecindarios_mas_costosos[i] = v.replace('&','and')

### Crear una escala de color de 0 a 148 de morado a rojo

In [473]:
colorscale = branca.colormap.linear.PuRd_09.scale(0, 148)

### Crear un diccionario de los vecindarios con los indices

In [474]:

d = {}
for i in range(len(vecindarios_mas_costosos)):
    d[vecindarios_mas_costosos[i]] = i


### Definir la función que pondrá color al mapa

In [475]:
def style_function_colores(feature):
    escala = 0
    vecindario_mapa = feature['properties']['neighbourhood']
    for vecindario_lista in vecindarios_mas_costosos:
        if vecindario_mapa in vecindario_lista:
            escala = d[vecindario_lista]
    if not escala:
        print(vecindario_mapa)
    return {
        'fillOpacity': 0.7,
        'weight': 0,
        'fillColor': colorscale(escala)
    }


### Generar el mapa con las coordenadas definidas arriba

In [476]:
mapa = folium.Map(location = london_coordinates,zoom_start = 12)

### crear el GeoJson encima del mapa y colorearlo con la funcion definida arriba

In [477]:
vecindarios_caros = folium.GeoJson(path_geojson,name='Vecindarios mas Caros',style_function=style_function_colores)

### Agregarlo como hijo a el mapa

In [478]:
mapa.add_child(vecindarios_caros)

### Agregar un layer control

In [401]:
mapa.add_child(folium.LayerControl())

### La siguiente línea de código hace un archivo HTML con el mapa que creamos en las anteriores líneas de código

In [264]:
mapa.save('mapa.html')

# MAPA DE LOS VECINDARIOS CON MEJORES REVIEWS

In [208]:
london_reviews = pd.read_csv('data/Londres/reviews.csv')

In [209]:
london_reviews.head(2)

listing_id      id        date  reviewer_id reviewer_name  \
0       13913   80770  2010-08-18       177109       Michael   
1       13913  367568  2011-07-11     19835707       Mathias   

                                            comments  
0  My girlfriend and I hadn't known Alina before ...  
1  Alina was a really good host. The flat is clea...

In [222]:
dummy = listings_london[['id','neighbourhood']]
dummy['listing_id'] = dummy['id']
dummy = dummy.drop('id',1)

C:\Users\Ricardo\Anaconda4\lib\site-packages\ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  


In [232]:
london_reviews = pd.merge(london_reviews,dummy,on = 'listing_id')

In [235]:
london_reviews['compound'] = np.nan
london_reviews.head(1)

listing_id     id        date  reviewer_id reviewer_name  \
0       13913  80770  2010-08-18       177109       Michael   

                                            comments    neighbourhood  \
0  My girlfriend and I hadn't known Alina before ...  LB of Islington   

   compound  
0       NaN

In [205]:
from vaderSentiment.vaderSentiment import SentimentIntensityAnalyzer
analyser = SentimentIntensityAnalyzer()

In [206]:
def sentiment_analyzer_scores(sentence):
    score = analyser.polarity_scores(sentence)
    return score

In [249]:
for i in range(len(london_reviews)):
    com = london_reviews.iloc[i,5]
    if(type(com)==str):
        c = sentiment_analyzer_scores(com)['compound']
        london_reviews.iloc[i,7]= c
london_reviews.head(20)

KeyboardInterrupt: 

In [479]:
vecindarios_reviews = list(london_reviews.groupby('neighbourhood')['compound'].mean().sort_values().index)
calificaciones = list(london_reviews.groupby('neighbourhood')['compound'].mean().sort_values())
for v in vecindarios_reviews:
    if '&' in v:
        i = vecindarios_reviews.index(v)
        vecindarios_reviews[i] = v.replace('&','and')

### Eliminar esta de abajo

In [480]:
calificaciones =calificaciones[:144]
vecindarios_reviews = vecindarios_reviews[:144]

In [481]:
colorscale2 = branca.colormap.linear.YlOrRd_09.scale(0.5, 1)

In [482]:
d2 = {}
for i in range(len(vecindarios_reviews)):
    d2[vecindarios_reviews[i]] = calificaciones[i]

In [483]:
def style_function_ratings(feature):
    escala2 = 0.5
    vecindario_mapa = feature['properties']['neighbourhood']
    for vecindario_lista in vecindarios_reviews:
        if vecindario_mapa in vecindario_lista:
            escala2 = d2[vecindario_lista]
    if (escala2 == 0.5):
        print(vecindario_mapa)
    return {
        'fillOpacity': 1,
        'weight': 0,
        'fillColor': colorscale2(escala2)
    }


In [484]:
vecindarios_good_rating = folium.GeoJson(path_geojson,name='Vecindarios mejores Ratings',style_function=style_function_ratings)

In [485]:
mapa.add_child(vecindarios_good_rating)

In [486]:
mapa.add_child(folium.LayerControl())

In [487]:
mapa.save('mapa.html')

In [497]:
listings_london.groupby('neighbourhood')['review_scores_rating'].mean().sort_values().describe()

count    149.000000
mean      93.042592
std        2.020763
min       87.606742
25%       91.965986
50%       93.214286
75%       94.361111
max       98.833333
Name: review_scores_rating, dtype: float64